In [1]:
import pandas as pd
import numpy as np
import random
from numpy.random import RandomState
from scipy import stats
from scipy.optimize import minimize
import scipy
import os
os.environ['R_HOME'] = '/Library/Frameworks/R.framework/Versions/4.1/Resources/'
import rpy2
from rpy2.robjects.packages import importr
from rpy2.robjects.packages import SignatureTranslatedAnonymousPackage
import datetime
from rpy2.robjects.vectors import FloatVector
from statsmodels.tsa.stattools import adfuller
from sklearn.linear_model import LinearRegression

real_data_folder = "/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_mixed_period_2000_2021/"
np.random.seed(22221)



yuima = importr("yuima")
n_stvol_sim_string = """
n_stvol = function(random_seed, num_sim,
                    mu11, mu21, mu22, mu31, mu41, mu42, 
                    sigma11, sigma12, sigma13, sigma14,
                    sigma21, sigma22, sigma23, sigma24,
                    sigma31, sigma32, sigma33, sigma34,
                    sigma41, sigma42, sigma43, sigma44,
                    xinit_vec, vinit_vec, T0, T, length){
  
  set.seed(random_seed)
  
  drift = c("mu11-(1/2)*(v1)^2", "mu21-mu22*v1", "mu31-(1/2)*(v2)^2", "mu41-mu42*v2")
  diffusion = matrix(c("sigma11*v1", "sigma12*v1", "sigma13*v1", "sigma14*v1", 
                       "sigma21", "sigma22", "sigma23", "sigma24", 
                       "sigma31*v2", "sigma32*v2", "sigma33*v2", "sigma34*v2", 
                       "sigma41", "sigma42", "sigma43", "sigma44"), 
                     4, 4, byrow=TRUE)
  
  stvol_model = setModel(drift=drift, diffusion=diffusion,
                          time.variable = "t",
                          state.variable=c("X1", "v1", "X2", "v2"),
                          solve.variable=c("X1", "v1", "X2", "v2"))
  newsamp = setSampling(Initial=T0, Terminal=T, n=length)
  
  n_sim_data = data.frame(matrix(nrow=length+1, ncol=2*num_sim))
  for (i in 1:num_sim){
    stvol_sim = simulate(stvol_model, 
                          true.par=list(
                            mu11=mu11, mu21=mu21, mu22=mu22, mu31=mu31, mu41=mu41, mu42=mu42,  
                            sigma11=sigma11, sigma12=sigma12, sigma13=sigma13, sigma14=sigma14,
                            sigma21=sigma21, sigma22=sigma22, sigma23=sigma23, sigma24=sigma24,
                            sigma31=sigma31, sigma32=sigma32, sigma33=sigma33, sigma34=sigma34,
                            sigma41=sigma41, sigma42=sigma42, sigma43=sigma43, sigma44=sigma44), 
                          xinit=c(xinit_vec[[i]][1], vinit_vec[[i]][1], xinit_vec[[i]][2], vinit_vec[[i]][2]), 
                          sampling=newsamp)
    original_data = stvol_sim@data@original.data
    one_sim_stvol = data.frame(original_data[,1], original_data[,3])
    colnames(one_sim_stvol) = c('series1', 'series2')
    n_sim_data[, (2*i-1):(2*i)] = one_sim_stvol
  }
  return(n_sim_data)
}
"""

n_stvol_sim = SignatureTranslatedAnonymousPackage(n_stvol_sim_string, "n_stvol_sim")
def n_stvol_simulation(random_seed, num_sim,
                        mu11, mu21, mu22, mu31, mu41, mu42, 
                        sigma11, sigma12, sigma13, sigma14,
                        sigma21, sigma22, sigma23, sigma24,
                        sigma31, sigma32, sigma33, sigma34,
                        sigma41, sigma42, sigma43, sigma44,
                        xinit_vec, vinit_vec, T0, T, length):

    n_sim_data = pd.DataFrame(
        n_stvol_sim.n_stvol(random_seed=random_seed, num_sim=num_sim,
                              mu11=mu11, mu21=mu21, mu22=mu22, mu31=mu31, mu41=mu41, mu42=mu42,  
                              sigma11=sigma11, sigma12=sigma12, sigma13=sigma13, sigma14=sigma14,
                              sigma21=sigma21, sigma22=sigma22, sigma23=sigma23, sigma24=sigma24,
                              sigma31=sigma31, sigma32=sigma32, sigma33=sigma33, sigma34=sigma34,
                              sigma41=sigma41, sigma42=sigma42, sigma43=sigma43, sigma44=sigma44,
                              xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=T0, T=T, length=length)).transpose()
    return n_sim_data



def price_to_log_price(n_price):
    return(np.log(n_price))

def log_price_to_price(n_log_price):
    return(np.exp(n_log_price))

def price_to_return(n_price):
    n_return = pd.DataFrame()
    for i in range(n_price.shape[1]):
        ith_column_price_series = n_price.iloc[:, i]
        n_return = pd.concat([n_return, 100 * (np.log(ith_column_price_series[1:].values) - np.log(ith_column_price_series[:-1]))], axis=1)
    return n_return

def log_price_to_return(n_log_price):
    n_real_return = pd.DataFrame()
    for i in range(n_log_price.shape[1]):
        ith_column_price_series = n_log_price.iloc[:, i]
        n_real_return = pd.concat([n_real_return, 100 * (ith_column_price_series[1:].values - ith_column_price_series[:-1])], axis=1)
    return n_real_return


def cross_corr_coef(lag_time_series, lead_time_series, lag):
    # calculate the cross correlation between two time series
    # if the result is not zero, then 'lead_time_series' leads 'lag_time_series'
    lag_time_series = lag_time_series.iloc[lag:]
    corr_coef = np.corrcoef(lag_time_series, lead_time_series.iloc[0:((lead_time_series.size)-lag)])[0][1]
    return corr_coef


def cal_stats(n_return, n_price):
    
    return_series1 = n_return.iloc[:, ::2]
    return_series2 = n_return.iloc[:, 1::2]
    price_series1 = n_price.iloc[:, ::2]
    price_series2 = n_price.iloc[:, 1::2]
    sq_return_series1 = return_series1**2
    sq_return_series2 = return_series2**2

    
    mean1 = return_series1.mean(axis=0).values
    sd1 = return_series1.std(axis=0).values
    skew1 = return_series1.skew(axis=0).values
    kurtosis1 = return_series1.kurtosis(axis=0).values
       
    
    mean2 = return_series2.mean(axis=0).values
    sd2 = return_series2.std(axis=0).values
    skew2 = return_series2.skew(axis=0).values
    kurtosis2 = return_series2.kurtosis(axis=0).values #8(8)
    
    
    
    # Autocorrelation of the 2 return series with 3 lags respectively
    autocorr1_lag_1 = return_series1.apply(lambda x: x.autocorr(lag=1))
    autocorr1_lag_2 = return_series1.apply(lambda x: x.autocorr(lag=2))
    autocorr1_lag_3 = return_series1.apply(lambda x: x.autocorr(lag=3))
    autocorr2_lag_1 = return_series2.apply(lambda x: x.autocorr(lag=1)) 
    autocorr2_lag_2 = return_series2.apply(lambda x: x.autocorr(lag=2)) 
    autocorr2_lag_3 = return_series2.apply(lambda x: x.autocorr(lag=3)) #6(14)
    
    # Cross-correlation between return series
    corr_ts1_lag_0 = []
    corr_ts1_lag_1 = [] # if not zero, return series 2 leads return series 1
    corr_ts1_lag_2 = []
    corr_ts1_lag_3 = []
    corr_ts2_lag_1 = [] # if not zero, return series 1 lead return series 2
    corr_ts2_lag_2 = []
    corr_ts2_lag_3 = []
    for i in range(int(real_price.shape[1]/2)):
        corr_ts1_lag_0.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 0))
        corr_ts1_lag_1.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 1))
        corr_ts1_lag_2.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 2))
        corr_ts1_lag_3.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 3))
        corr_ts2_lag_1.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 1))
        corr_ts2_lag_2.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 2))
        corr_ts2_lag_3.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 3))
    corr_ts1_lag_0 = pd.Series(corr_ts1_lag_0)
    corr_ts1_lag_1 = pd.Series(corr_ts1_lag_1)
    corr_ts1_lag_2 = pd.Series(corr_ts1_lag_2)
    corr_ts1_lag_3 = pd.Series(corr_ts1_lag_3)
    corr_ts2_lag_1 = pd.Series(corr_ts2_lag_1)
    corr_ts2_lag_2 = pd.Series(corr_ts2_lag_2)
    corr_ts2_lag_3 = pd.Series(corr_ts2_lag_3)#7(21)
    
    
    
    # Autocorrelation of the 2 squared returns with 3 lags respectively
    autocorr_sqreturn_1_lag_1 = sq_return_series1.apply(lambda x: x.autocorr(lag=1))
    autocorr_sqreturn_1_lag_2 = sq_return_series1.apply(lambda x: x.autocorr(lag=2))
    autocorr_sqreturn_1_lag_3 = sq_return_series1.apply(lambda x: x.autocorr(lag=3))
    autocorr_sqreturn_2_lag_1 = sq_return_series2.apply(lambda x: x.autocorr(lag=1)) 
    autocorr_sqreturn_2_lag_2 = sq_return_series2.apply(lambda x: x.autocorr(lag=2)) 
    autocorr_sqreturn_2_lag_3 = sq_return_series2.apply(lambda x: x.autocorr(lag=3))#6(27)
    
    # Cross-correlation between squared returns series
    corr_sqts1_lag_0 = []
    corr_sqts1_lag_1 = [] # if not zero, return series 2 leads return series 1
    corr_sqts1_lag_2 = []
    corr_sqts1_lag_3 = []
    corr_sqts2_lag_1 = [] # if not zero, return series 1 lead return series 2
    corr_sqts2_lag_2 = []
    corr_sqts2_lag_3 = []
    for i in range(int(real_price.shape[1]/2)):
        corr_sqts1_lag_0.append(cross_corr_coef(sq_return_series1.iloc[:, i], sq_return_series2.iloc[:, i], 0))
        corr_sqts1_lag_1.append(cross_corr_coef(sq_return_series1.iloc[:, i], sq_return_series2.iloc[:, i], 1))
        corr_sqts1_lag_2.append(cross_corr_coef(sq_return_series1.iloc[:, i], sq_return_series2.iloc[:, i], 2))
        corr_sqts1_lag_3.append(cross_corr_coef(sq_return_series1.iloc[:, i], sq_return_series2.iloc[:, i], 3))
        corr_sqts2_lag_1.append(cross_corr_coef(sq_return_series2.iloc[:, i], sq_return_series1.iloc[:, i], 1))
        corr_sqts2_lag_2.append(cross_corr_coef(sq_return_series2.iloc[:, i], sq_return_series1.iloc[:, i], 2))
        corr_sqts2_lag_3.append(cross_corr_coef(sq_return_series2.iloc[:, i], sq_return_series1.iloc[:, i], 3))
    corr_sqts1_lag_0 = pd.Series(corr_ts1_lag_0)
    corr_sqts1_lag_1 = pd.Series(corr_ts1_lag_1)
    corr_sqts1_lag_2 = pd.Series(corr_ts1_lag_2)
    corr_sqts1_lag_3 = pd.Series(corr_ts1_lag_3)
    corr_sqts2_lag_1 = pd.Series(corr_ts2_lag_1)
    corr_sqts2_lag_2 = pd.Series(corr_ts2_lag_2)
    corr_sqts2_lag_3 = pd.Series(corr_ts2_lag_3)#7(34)
    
    
    
    
    stats_data = pd.DataFrame([mean1, mean2, sd1, sd2, 
                               skew1, skew2, kurtosis1, kurtosis2, #8(8)
                               
                               autocorr1_lag_1, autocorr1_lag_2, autocorr1_lag_3,
                               autocorr2_lag_1, autocorr2_lag_2, autocorr2_lag_3,#6(14)
                               
                               corr_ts1_lag_0, 
                               corr_ts1_lag_1, corr_ts1_lag_2, corr_ts1_lag_3,
                               corr_ts2_lag_1, corr_ts2_lag_2, corr_ts2_lag_3, #7(21)
                               
                               autocorr_sqreturn_1_lag_1, autocorr_sqreturn_1_lag_2, autocorr_sqreturn_1_lag_3,
                               autocorr_sqreturn_2_lag_1, autocorr_sqreturn_2_lag_2, autocorr_sqreturn_2_lag_3,#6(27)
                               
                               corr_sqts1_lag_0,
                               corr_sqts1_lag_1, corr_sqts1_lag_2, corr_sqts1_lag_3,
                               corr_sqts2_lag_1, corr_sqts2_lag_2, corr_sqts2_lag_3])#7(34)
    stats_data = stats_data.transpose()
    stats_data.columns = [
        'return_mean1', 'return_mean2',
        'return_sd1', 'return_sd2',
        'return_skew1', 'return_skew2',
        'return_kurtosis1', 'return_kurtosis2',
        
        'return_autocorrelation_ts1_lag1', 'return_autocorrelation_ts1_lag2', 'return_autocorrelation_ts1_lag3',
        'return_autocorrelation_ts2_lag1', 'return_autocorrelation_ts2_lag2', 'return_autocorrelation_ts2_lag3',
        
        'return_correlation_ts1_lag_0',
        'return_correlation_ts1_lag_1', 'return_correlation_ts1_lag_2', 'return_correlation_ts1_lag_3',
        'return_correlation_ts2_lag_1', 'return_correlation_ts2_lag_2', 'return_correlation_ts2_lag_3',
        
        'sqreturn_autocorrelation_ts1_lag1', 'sqreturn_autocorrelation_ts1_lag2', 'sqreturn_autocorrelation_ts1_lag3',
        'sqreturn_autocorrelation_ts2_lag1', 'sqreturn_autocorrelation_ts2_lag2', 'sqreturn_autocorrelation_ts2_lag3',
    
        'sqreturn_correlation_ts1_lag_0',
        'sqreturn_correlation_ts1_lag_1', 'sqreturn_correlation_ts1_lag_2', 'sqreturn_correlation_ts1_lag_3', 
        'sqreturn_correlation_ts2_lag_1', 'sqreturn_correlation_ts2_lag_2', 'sqreturn_correlation_ts2_lag_3']
    
    return stats_data


def loss_function(params):

    params = FloatVector(params)
    print(params)
    moment_loss = pd.DataFrame().reindex_like(real_stats)

    n_real_log_price = n_stvol_simulation(
        random_seed=int(np.random.randint(low=0, high=980608, size=(1,))), num_sim=num_sim,
        mu11=mu11, 
        mu21=mu21, mu22=mu22, 
        mu31=mu31, 
        mu41=mu41, mu42=mu42,  
        sigma11=sigma11, sigma12=sigma12, sigma13=sigma13, sigma14=sigma14,
        sigma21=sigma21, sigma22=sigma22, sigma23=sigma23, sigma24=sigma24,
        sigma31=sigma31, sigma32=sigma32, sigma33=sigma33, sigma34=sigma34,
        sigma41=sigma41, sigma42=sigma42, sigma43=sigma43, sigma44=sigma44,
        xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=T0, T=T, length=length)


    n_real_price = log_price_to_price(n_real_log_price)
    n_real_return = price_to_return(n_real_price)
    n_real_stats = cal_stats(n_real_return, n_real_price)
    
    
    n_sim_log_price = n_stvol_simulation(
        random_seed=int(np.random.randint(low=0, high=980608, size=(1,))), num_sim=num_sim,
        mu11=params[0], 
        mu21=params[1], mu22=params[2], 
        mu31=params[3], 
        mu41=params[4], mu42=params[5],  
        sigma11=params[6],  sigma12=params[7],  sigma13=params[8],  sigma14=params[9],
        sigma21=params[10], sigma22=params[11], sigma23=params[12], sigma24=params[13],
        sigma31=params[14], sigma32=params[15], sigma33=params[16], sigma34=params[17],
        sigma41=params[18], sigma42=params[19], sigma43=params[20], sigma44=params[21],
        xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=T0, T=T, length=length)


    n_sim_price = log_price_to_price(n_sim_log_price)
    n_sim_return = price_to_return(n_sim_price)
    n_sim_stats = cal_stats(n_sim_return, n_sim_price)


    moment_loss = np.abs(n_real_stats - n_sim_stats)
    sum_loss = np.sum(moment_loss)
    
    sum_loss[6] = sum_loss[6]/10 
    sum_loss[7] = sum_loss[7]/10 
    
    loss = np.sum(sum_loss)
    
    print(sum_loss)
    print(loss)
    print('----------')

    return loss



mu11, mu21, mu22, mu31, mu41, mu42 = 0.97963193, 2.18613961, 1.32649913, 0.59072948, 1.81251381, 1.21533049
sigma11, sigma12, sigma13, sigma14 = 0.25450407, 0.01790030, 0.06813574, 0.04945842
sigma21, sigma22, sigma23, sigma24 = 0.45787254, 0.44836582, 0.22869755, 0.25556408 
sigma31, sigma32, sigma33, sigma34 = 0.02821395, 0.09632337, 0.19785619, 0.17488319
sigma41, sigma42, sigma43, sigma44 = 0.43697182, 0.11065608, 0.25486800, 0.30596497


real_price = pd.read_csv(real_data_folder + "pair_prices_cal.csv", index_col=[0])
real_log_price = price_to_log_price(n_price=real_price)
real_return = pd.read_csv(real_data_folder + "pair_returns_cal.csv", index_col=[0])
real_stats = cal_stats(n_return=real_return, n_price=real_price)


xinit_vec = []
vinit_vec = []
for i in range(int(real_price.shape[1]/2)):

    init_pair_log_price = [real_log_price.iloc[0, 2*i], real_log_price.iloc[0, 2*i+1]]
    init_pair_log_price = FloatVector(init_pair_log_price)
    xinit_vec.append(init_pair_log_price)
    
    init_pair_volatility = [np.std(real_return.iloc[:, 2*i]/100), np.std(real_return.iloc[:, 2*i+1]/100)]
    init_pair_volatility = FloatVector(init_pair_volatility)
    vinit_vec.append(init_pair_volatility)
    
num_sim, T0, T, length = real_stats.shape[0], 0, 2, real_price.shape[0]



initial0 = [0.1, 
            1, 1, 
            0.1, 
            1, 1,
            0.1, 0.1, 0.1, 0.1,
            0.1, 0.1, 0.1, 0.1,
            0.1, 0.1, 0.1, 0.1,
            0.1, 0.1, 0.1, 0.1]
begin_time = datetime.datetime.now()
res = minimize(loss_function, initial0, method='Powell',
               tol=1e-6, options={'disp': True},
               bounds=[(0, None), 
                       (None, None), (None, None), 
                       (0, None), 
                       (None, None), (None, None),
                       (0, None), (0, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None)])
print(res.x)

time = datetime.datetime.now() - begin_time
print(time)

params = (res.x)
loss = loss_function((params))
print(loss)

 [1] 0.1 1.0 1.0 0.1 1.0 1.0 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1
[20] 0.1 0.1 0.1

return_mean1                          39.363505
return_mean2                          20.682198
return_sd1                           287.777364
return_sd2                           256.415080
return_skew1                          55.139081
return_skew2                          50.690211
return_kurtosis1                      22.374231
return_kurtosis2                      24.899828
return_autocorrelation_ts1_lag1       15.057891
return_autocorrelation_ts1_lag2       14.951853
return_autocorrelation_ts1_lag3       15.678838
return_autocorrelation_ts2_lag1       15.310243
return_autocorrelation_ts2_lag2       15.054713
return_autocorrelation_ts2_lag3       14.626308
return_correlation_ts1_lag_0         145.348062
return_correlation_ts1_lag_1          14.694948
return_correlation_ts1_lag_2          14.026934
return_correlation_ts1_lag_3          14.739119
return_correlation_ts2_lag_1         

return_mean1                          48.933279
return_mean2                          20.044406
return_sd1                           318.980475
return_sd2                           273.579018
return_skew1                          54.908845
return_skew2                          54.584601
return_kurtosis1                      24.665419
return_kurtosis2                      22.875591
return_autocorrelation_ts1_lag1       15.036540
return_autocorrelation_ts1_lag2       15.110872
return_autocorrelation_ts1_lag3       15.262080
return_autocorrelation_ts2_lag1       14.806656
return_autocorrelation_ts2_lag2       14.885871
return_autocorrelation_ts2_lag3       15.187835
return_correlation_ts1_lag_0         145.687674
return_correlation_ts1_lag_1          14.055965
return_correlation_ts1_lag_2          16.066134
return_correlation_ts1_lag_3          15.786481
return_correlation_ts2_lag_1          15.307050
return_correlation_ts2_lag_2          14.971728
return_correlation_ts2_lag_3          15

return_mean1                          31.365354
return_mean2                          19.523342
return_sd1                           310.758410
return_sd2                           270.893259
return_skew1                          56.097264
return_skew2                          54.321571
return_kurtosis1                      21.295433
return_kurtosis2                      22.140255
return_autocorrelation_ts1_lag1       15.395137
return_autocorrelation_ts1_lag2       14.044887
return_autocorrelation_ts1_lag3       14.281633
return_autocorrelation_ts2_lag1       15.957427
return_autocorrelation_ts2_lag2       15.765572
return_autocorrelation_ts2_lag3       14.784267
return_correlation_ts1_lag_0         146.443236
return_correlation_ts1_lag_1          15.421304
return_correlation_ts1_lag_2          15.326455
return_correlation_ts1_lag_3          15.065610
return_correlation_ts2_lag_1          15.144066
return_correlation_ts2_lag_2          14.338026
return_correlation_ts2_lag_3          15

return_mean1                          30.903001
return_mean2                          19.111164
return_sd1                           316.256003
return_sd2                           276.819357
return_skew1                          57.487328
return_skew2                          51.993615
return_kurtosis1                      21.993469
return_kurtosis2                      21.308747
return_autocorrelation_ts1_lag1       14.518247
return_autocorrelation_ts1_lag2       15.529581
return_autocorrelation_ts1_lag3       16.118802
return_autocorrelation_ts2_lag1       15.552341
return_autocorrelation_ts2_lag2       15.348776
return_autocorrelation_ts2_lag3       15.844693
return_correlation_ts1_lag_0         144.917863
return_correlation_ts1_lag_1          14.799930
return_correlation_ts1_lag_2          15.355263
return_correlation_ts1_lag_3          15.643328
return_correlation_ts2_lag_1          14.879480
return_correlation_ts2_lag_2          15.817216
return_correlation_ts2_lag_3          17

return_mean1                          30.458588
return_mean2                          19.717569
return_sd1                           289.670972
return_sd2                           250.335476
return_skew1                          57.397160
return_skew2                          59.331955
return_kurtosis1                      23.521749
return_kurtosis2                      21.978998
return_autocorrelation_ts1_lag1       15.450814
return_autocorrelation_ts1_lag2       15.371187
return_autocorrelation_ts1_lag3       15.707755
return_autocorrelation_ts2_lag1       14.543232
return_autocorrelation_ts2_lag2       14.467327
return_autocorrelation_ts2_lag3       16.020779
return_correlation_ts1_lag_0         145.675315
return_correlation_ts1_lag_1          14.880444
return_correlation_ts1_lag_2          14.928078
return_correlation_ts1_lag_3          15.924442
return_correlation_ts2_lag_1          15.971083
return_correlation_ts2_lag_2          15.815978
return_correlation_ts2_lag_3          14

...

return_mean1                          47.283548
return_mean2                          22.997447
return_sd1                           135.743893
return_sd2                           137.190145
return_skew1                          59.536297
return_skew2                          58.724742
return_kurtosis1                      24.204279
return_kurtosis2                      27.327071
return_autocorrelation_ts1_lag1       14.283523
return_autocorrelation_ts1_lag2       14.248732
return_autocorrelation_ts1_lag3       16.204207
return_autocorrelation_ts2_lag1       13.714131
return_autocorrelation_ts2_lag2       15.644511
return_autocorrelation_ts2_lag3       15.464875
return_correlation_ts1_lag_0          35.994305
return_correlation_ts1_lag_1          14.133560
return_correlation_ts1_lag_2          13.986235
return_correlation_ts1_lag_3          16.285091
return_correlation_ts2_lag_1          14.531946
return_correlation_ts2_lag_2          14.372168
return_correlation_ts2_lag_3          15

return_mean1                          47.954200
return_mean2                          21.229132
return_sd1                           136.154554
return_sd2                           135.617991
return_skew1                          58.960475
return_skew2                          58.281043
return_kurtosis1                      24.773254
return_kurtosis2                      25.811586
return_autocorrelation_ts1_lag1       15.161057
return_autocorrelation_ts1_lag2       15.243940
return_autocorrelation_ts1_lag3       13.953532
return_autocorrelation_ts2_lag1       14.841672
return_autocorrelation_ts2_lag2       15.241049
return_autocorrelation_ts2_lag3       14.883602
return_correlation_ts1_lag_0          36.769657
return_correlation_ts1_lag_1          15.509218
return_correlation_ts1_lag_2          14.313316
return_correlation_ts1_lag_3          14.653606
return_correlation_ts2_lag_1          15.580964
return_correlation_ts2_lag_2          16.188831
return_correlation_ts2_lag_3          15

return_mean1                          48.053943
return_mean2                          22.554197
return_sd1                           141.667782
return_sd2                           138.187931
return_skew1                          66.095583
return_skew2                          61.333745
return_kurtosis1                      27.216397
return_kurtosis2                      32.264862
return_autocorrelation_ts1_lag1       15.728123
return_autocorrelation_ts1_lag2       15.847781
return_autocorrelation_ts1_lag3       15.030076
return_autocorrelation_ts2_lag1       16.356238
return_autocorrelation_ts2_lag2       15.984763
return_autocorrelation_ts2_lag3       15.814103
return_correlation_ts1_lag_0          36.481196
return_correlation_ts1_lag_1          15.836841
return_correlation_ts1_lag_2          14.954567
return_correlation_ts1_lag_3          15.068626
return_correlation_ts2_lag_1          15.406776
return_correlation_ts2_lag_2          17.494246
return_correlation_ts2_lag_3          16

return_mean1                          51.749269
return_mean2                          21.923249
return_sd1                           138.641089
return_sd2                           134.105337
return_skew1                          64.509756
return_skew2                          62.498906
return_kurtosis1                      26.463593
return_kurtosis2                      30.239376
return_autocorrelation_ts1_lag1       15.908200
return_autocorrelation_ts1_lag2       15.210316
return_autocorrelation_ts1_lag3       14.877794
return_autocorrelation_ts2_lag1       13.978917
return_autocorrelation_ts2_lag2       16.159807
return_autocorrelation_ts2_lag3       15.456886
return_correlation_ts1_lag_0          36.927522
return_correlation_ts1_lag_1          15.117195
return_correlation_ts1_lag_2          17.321458
return_correlation_ts1_lag_3          15.730676
return_correlation_ts2_lag_1          15.755374
return_correlation_ts2_lag_2          15.264964
return_correlation_ts2_lag_3          14

return_mean1                          44.104990
return_mean2                          21.949562
return_sd1                           128.879078
return_sd2                           128.304751
return_skew1                          71.291629
return_skew2                          61.276800
return_kurtosis1                      28.142422
return_kurtosis2                      29.561484
return_autocorrelation_ts1_lag1       14.851276
return_autocorrelation_ts1_lag2       14.151545
return_autocorrelation_ts1_lag3       15.723339
return_autocorrelation_ts2_lag1       15.912387
return_autocorrelation_ts2_lag2       15.399865
return_autocorrelation_ts2_lag3       14.397962
return_correlation_ts1_lag_0          35.988030
return_correlation_ts1_lag_1          15.500332
return_correlation_ts1_lag_2          14.567201
return_correlation_ts1_lag_3          15.158275
return_correlation_ts2_lag_1          14.409158
return_correlation_ts2_lag_2          14.570081
return_correlation_ts2_lag_3          15

In [2]:
mu11, mu21, mu22, mu31, mu41, mu42 = 0.97963193, 2.18613961, 1.32649913, 0.59072948, 1.81251381, 1.21533049
sigma11, sigma12, sigma13, sigma14 = 0.25450407, 0.01790030, 0.06813574, 0.04945842
sigma21, sigma22, sigma23, sigma24 = 0.45787254, 0.44836582, 0.22869755, 0.25556408 
sigma31, sigma32, sigma33, sigma34 = 0.02821395, 0.09632337, 0.19785619, 0.17488319
sigma41, sigma42, sigma43, sigma44 = 0.43697182, 0.11065608, 0.25486800, 0.30596497
  
print(params)

[1.09937501 2.35848939 2.26344386 0.37629547 1.87986377 1.74093028
 0.30045806 0.0505722  0.12596615 0.21815988 0.33746252 0.27827578
 0.45769939 0.20632456 0.10853399 0.32232501 0.12217301 0.07896252
 0.34540139 0.22418998 0.45481673 0.24772659]
